In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import plotly.graph_objects as go
from tqdm import trange

In [33]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from tqdm import trange

class hedging_strategy():

    def __init__(self, period, ALPHA=0.5, GAMMA=1, epsilon = 0.1):
        self.ALPHA = ALPHA # step size of Q-learning
        self.GAMMA = GAMMA # discount rate of Q-learning
        self.Actions = [0, 0.5, 1] # possible actions: 0: short 0 stocks, 0.5: short 0.5 stocks, 1: short 1 stocks
        self.epsilon = epsilon
        self.up = 1.1 # the upside ratio of stock movement in binominal model
        self.down = 0.9 # the downside ratio of stock movement in binominal model
        self.period = period
        self.start_price = self.period-1 ## we use a np.array(2*T-1) to store the corresponding price, so the start price should be the T-1 element in the array


        ### Here we define state as the tuple (price(St), time(t))

    def choose_action(self, state, q_value, epsilon):
        # choose action based on epsilon-greedy algorithm. Here we take epsilon as input so that we can adjust epsilon according to different episodes
        if np.random.binomial(1, epsilon) == 1:
            ## exploration
            action = np.random.choice([0,1,2])
        else:
            ## exploitation
            values_ = q_value[state[0], state[1], :]
            action = np.random.choice([action_ for action_, value_ in enumerate(values_) if value_ == np.max(values_)])
        return action

    def step(self, state, action):
        ## each step, input a state and action, return next state and reward
        movement = np.random.binomial(1, 0.5)

        if movement == 1:
            next_price = state[0] + 1
        elif movement == 0:
            next_price = state[0] - 1

        if state[0] - self.start_price > 0:
            up_times = state[0] - self.start_price + (state[1] - (state[0] - self.start_price))/2
        else:
            up_times = (state[1] + (state[0] - self.start_price))/2
        down_times = state[1] - up_times

        St = self.up**up_times * self.down**down_times # stock price at time t
        St_1 = float(np.where(next_price>state[0], St*self.up, St*self.down)) # stock price at time t+1


        reward = (St_1 - St) + self.Actions[action]*(St - St_1) ## long_position(1) * (St+1- St) + short_position*(St-St+1)
        t = state[1]+1

        next_state = [next_price, t]
        return next_state, reward

    def q_learning(self, q_value, epsilon):
        price = self.period-1
        t = 0
        state = [price,t]
        rewards = 0

        while state[1] < self.period:
            #action = choose_action(state, q_value)
            action = self.choose_action(state, q_value, epsilon)
            next_state, reward = self.step(state, action)
            rewards += reward
            # Q-Learning update
            if state[1] < self.period-1:
                q_value[state[0],state[1], action] += self.ALPHA * (
                        reward + self.GAMMA * np.max(q_value[next_state[0],next_state[1],:]) -
                        q_value[state[0],state[1], action])
            else:
                ## if t == T-1, means the next state is the terminal state t=T. we set all Q(:, T, :) = 0)
                q_value[state[0],state[1], action] += self.ALPHA * (
                        reward + 0 -
                        q_value[state[0],state[1], action])

            state = next_state
        return q_value, rewards


    # print optimal policy
    def print_optimal_policy(self):
        q_value = self.q_value
        optimal_policy = []
        for i in range(0, np.shape(q_value)[0]):
            optimal_policy.append([])
            for j in range(0, np.shape(q_value)[1]):
                bestAction = np.argmax(q_value[i, j, :])
                if ~np.any(q_value[i, j, :]):
                    ## if q_value is all zero, it means this state(price, time) is not availabel in the binominal model
                    optimal_policy[-1].append('')
                elif bestAction == 0:
                    optimal_policy[-1].append('0')
                elif bestAction == 1:
                    optimal_policy[-1].append('-0.5')
                elif bestAction == 2:
                    optimal_policy[-1].append('-1')
        res = []
        for row in optimal_policy:
            res.append(row)
        return res

    def train(self, episodes = 100000):
        T = self.period
        q_value = np.zeros((2*T-1, T , 3))
        reward_record = []
        epsilon = self.epsilon
        for j in trange(episodes):
            if j %1000 == 0:
                epsilon *= 0.8
            q_value, rewards = self.q_learning(q_value, epsilon)
            reward_record.append(rewards)
        self.q_value = q_value
        self.reward_record = np.array(reward_record)

    def plot_training(self):
        plt.plot(self.reward_record)
        plt.title('rewards against traning episodes')
        plt.xlabel('episodes')
        plt.ylabel('rewards')

    def get_q_value(self):
        return self.q_value

    def compare_results(self, runs = 1000):
        rewards_optimal = []
        rewards_0 = []
        rewards_half = []
        rewards_1 = []
        rewards_random = []



        for i in trange(runs):

            price = self.period-1
            t = 0
            state = [price,t]

            reward_optimal, reward_0, reward_half, reward_1, reward_random = 0, 0, 0, 0, 0

            while state[1] < self.period:
                movement = np.random.binomial(1, 0.5)

                if movement == 1:
                    next_price = state[0] + 1
                elif movement == 0:
                    next_price = state[0] - 1

                if state[0] - self.start_price > 0:
                    up_times = state[0] - self.start_price + (state[1] - (state[0] - self.start_price))/2
                else:
                    up_times = (state[1] + (state[0] - self.start_price))/2
                down_times = state[1] - up_times

                St = self.up**up_times * self.down**down_times # stock price at time t
                St_1 = float(np.where(next_price>state[0], St*self.up, St*self.down)) # stock price at time t+1

                optimal_action =  np.argmax(self.q_value[state[0], state[1], :])
                reward_optimal += ((St_1 - St) + self.Actions[optimal_action]*(St - St_1))
                reward_0 += (St_1 - St)
                reward_half += ((St_1 - St) + self.Actions[1]*(St - St_1))
                reward_1 += ((St_1 - St) + self.Actions[2]*(St - St_1))
                reward_random += ((St_1 - St) + self.Actions[np.random.choice([0,1,2])]*(St - St_1))

                t = state[1]+1
                next_state = [next_price, t]
                state = next_state

            rewards_optimal.append(reward_optimal)
            rewards_0.append(reward_0)
            rewards_half.append(reward_half)
            rewards_1.append(reward_1)
            rewards_random.append(reward_random)

        rewards_optimal = np.array(rewards_optimal)
        rewards_0 = np.array(rewards_0)
        rewards_half = np.array(rewards_half)
        rewards_1 = np.array(rewards_1)
        rewards_random = np.array(rewards_random)

        return [rewards_optimal, rewards_0, rewards_half, rewards_1, rewards_random]

In [31]:
solver = hedging_strategy(5)
solver.train()
temp = solver.print_optimal_policy()
q_value = solver.get_q_value()
temp2 = solver.compare_results(10000)

100%|██████████| 10000/10000 [00:01<00:00, 8701.69it/s]


In [34]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
import numpy as np

y1 = temp2[1]
y2 = temp2[2]
y3 = temp2[4]

x = np.arange(1,10001)

colors = ['#3f3f3f', '#00bfff', '#ff7f00']

fig = make_subplots(
    rows=3, cols=2,
    column_widths=[0.55, 0.45],
    row_heights=[1., 1., 1.],
    specs=[[{"type": "scatter"}, {"type": "xy"}],
           [{"type": "scatter"},            {"type": "xy", "rowspan": 2}           ],
           [{"type": "scatter"},            None           ]])

fig.add_trace(
    go.Scatter(x = x,
                y = y1.cumsum()/x,
                hoverinfo = 'x+y',
                mode='lines',
                line=dict(color='#3f3f3f',
                width=1),
                showlegend=False,
                ),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x = x,
                y = y2.cumsum()/x,
                hoverinfo = 'x+y',
                mode='lines',
                line=dict(color='#00bfff',
                width=1),
                showlegend=False,
                ),
    row=2, col=1
)

fig.add_trace(
    go.Scatter(x = x,
                y = y3.cumsum()/x,
                hoverinfo = 'x+y',
                mode='lines',
                line=dict(color='#ff7f00',
                width=1),
                showlegend=False,
                ),
    row=3, col=1
)

boxfig= go.Figure(data=[go.Box(x=y1, showlegend=False, notched=True, marker_color="#3f3f3f", name='3'),
                        go.Box(x=y2, showlegend=False, notched=True, marker_color="#00bfff", name='2'),
                        go.Box(x=y3, showlegend=False, notched=True, marker_color="#ff7f00", name='1')])

for k in range(len(boxfig.data)):
     fig.add_trace(boxfig.data[k], row=1, col=2)

group_labels = ['Alway0', 'Alway0.5', 'Random']
hist_data = [y1, y2, y3]

distplfig = ff.create_distplot(hist_data, group_labels, colors=colors,
                         bin_size=.2, show_rug=False)

for k in range(len(distplfig.data)):
    fig.add_trace(distplfig.data[k],
    row=2, col=2
)
fig.update_layout(barmode='overlay')
fig.show()

In [41]:
res = pd.DataFrame(temp2[1:]).transpose()

In [42]:
res.columns=['Alway0', 'Alway0.5','Alway1(Optimal)', 'Random']

In [45]:
res.quantile(0.05)

Alway0            -0.2810
Alway0.5          -0.1405
Alway1(Optimal)    0.0000
Random            -0.2200
Name: 0.05, dtype: float64

In [48]:
res[res<res.quantile(0.05)].mean()

Alway0            -0.409510
Alway0.5          -0.204755
Alway1(Optimal)         NaN
Random            -0.259823
dtype: float64

In [49]:
res.std()

Alway0             0.225844
Alway0.5           0.112922
Alway1(Optimal)    0.000000
Random             0.145006
dtype: float64

In [35]:
fig = go.Figure(data=go.Heatmap(
                   z=temp,

                   hoverongaps = False))  # 缺失值处理参数
fig.show()

